# Optuna一种超参数优化框架
https://github.com/optuna/optuna

分别采用两组数据集进行比较，分别是加利福尼亚住房数据集（回归）和森林植被类型（多分类）

## 结论：效果不错

## 波士顿房价预测任务（回归）

In [1]:
import numpy as np
import pandas as pd
import time
import gc

from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import lightgbm as lgb  # 使用lgb模型

In [2]:
from sklearn.datasets import fetch_california_housing
data = fetch_california_housing()
X, y = data['data'], data['target']

In [3]:
X = pd.DataFrame(X,columns=data.feature_names)
X.head(2)

MedInc  HouseAge  AveRooms  AveBedrms  Population  AveOccup  Latitude  \
0  8.3252      41.0  6.984127    1.02381       322.0  2.555556     37.88   
1  8.3014      21.0  6.238137    0.97188      2401.0  2.109842     37.86   

   Longitude  
0    -122.23  
1    -122.22

In [4]:
X.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 20640 entries, 0 to 20639
Data columns (total 8 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   MedInc      20640 non-null  float64
 1   HouseAge    20640 non-null  float64
 2   AveRooms    20640 non-null  float64
 3   AveBedrms   20640 non-null  float64
 4   Population  20640 non-null  float64
 5   AveOccup    20640 non-null  float64
 6   Latitude    20640 non-null  float64
 7   Longitude   20640 non-null  float64
dtypes: float64(8)
memory usage: 1.3 MB


In [5]:
# 切分训练和测试集
train_x, test_x, train_y, test_y = train_test_split(X, y,random_state=42,test_size=0.1)
train_y = pd.DataFrame(train_y,columns=['result'])
test_y = pd.DataFrame(test_y,columns=['result'])

print('训练集：',train_x.shape)
print('测试集：', test_x.shape)

训练集： (18576, 8)
测试集： (2064, 8)


In [6]:
from sklearn.model_selection import KFold
skf = KFold(n_splits=5, shuffle=True, random_state=42)

### 使用LGB作为模型并CV，不使用optuna调参

In [7]:
%%time
test_predict = np.zeros(shape=[test_x.shape[0], 5],dtype=float)
params = {'boosting_type': 'gbdt',
          'objective': 'regression',
          "metric": 'rmse'}
for i, (trn_idx, val_idx) in enumerate(skf.split(train_x, train_y)):
    dtrain = lgb.Dataset(train_x.iloc[trn_idx], label=train_y.iloc[trn_idx])
    dvalid = lgb.Dataset(train_x.iloc[val_idx], label=train_y.iloc[val_idx])
    model = lgb.train(params=params, train_set=dtrain,valid_sets=[dvalid],
                      verbose_eval=50,
                      early_stopping_rounds=20,
                      num_boost_round=5000)
    test_predict[:,i] = model.predict(test_x)
predict = np.mean(test_predict,axis=1)

[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000866 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1837
[LightGBM] [Info] Number of data points in the train set: 14860, number of used features: 8
[LightGBM] [Info] Start training from score 2.073247
Training until validation scores don't improve for 20 rounds
[50]	valid_0's rmse: 0.492877
[100]	valid_0's rmse: 0.469235
[150]	valid_0's rmse: 0.460357
[200]	valid_0's rmse: 0.455302
[250]	valid_0's rmse: 0.452674
[300]	valid_0's rmse: 0.451179
Early stopping, best iteration is:
[313]	valid_0's rmse: 0.450303
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000494 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1838
[LightGBM] [Info] Number of data points in the train set: 14861, number of used features: 8
[LightGBM] [Info] Start training from score 2.070396


In [8]:
# 评估指标rmse，越小越好
np.sqrt(mean_squared_error(test_y,predict))

0.4346521330333544

### 使用LGB作为模型并CV，使用optuna调参

In [9]:
# pip install optuna

In [10]:
import optuna

In [11]:
def objective(trial,train_x, train_y, valid_x, valid_y):
    dtrain = lgb.Dataset(train_x, label=train_y)
    dvalid = lgb.Dataset(valid_x, label=valid_y)

    param = {
        "objective": "regression",
        "metric": "rmse",
        "verbosity": -1,
        "boosting_type": "gbdt",
        'random_state':42,
        "lambda_l1": trial.suggest_float("lambda_l1", 1e-8, 10.0, log=True),
        "lambda_l2": trial.suggest_float("lambda_l2", 1e-8, 10.0, log=True),
        "num_leaves": trial.suggest_int("num_leaves", 2, 256),
        "feature_fraction": trial.suggest_float("feature_fraction", 0.4, 1.0),
        "bagging_fraction": trial.suggest_float("bagging_fraction", 0.4, 1.0),
        "bagging_freq": trial.suggest_int("bagging_freq", 1, 7),
        "min_child_samples": trial.suggest_int("min_child_samples", 5, 100),
    }

    # Add a callback for pruning.
    pruning_callback = optuna.integration.LightGBMPruningCallback(trial, "rmse")
    gbm = lgb.train(
        param, dtrain, valid_sets=[dvalid], verbose_eval=False, callbacks=[pruning_callback]
    )

    preds = gbm.predict(valid_x)
    pred_labels = np.rint(preds)
    rmse = np.sqrt(mean_squared_error(valid_y,pred_labels))
    return rmse

In [12]:
%%time
if __name__ == "__main__":
    test_predict = np.zeros(shape=[test_x.shape[0], 5],dtype=float)
    study = optuna.create_study(
        pruner=optuna.pruners.MedianPruner(n_warmup_steps=10), direction="minimize"  # 指定是越小越好
    )
    for i, (trn_idx, val_idx) in enumerate(skf.split(train_x, train_y)):
        study.optimize(lambda trial: objective(trial, train_x.iloc[trn_idx], train_y.iloc[trn_idx], 
                                               train_x.iloc[val_idx], train_y.iloc[val_idx]), n_trials=100)

        print("Number of finished trials: {}".format(len(study.trials)))

        print("Best trial:")
        trial = study.best_trial

        print("  Value: {}".format(trial.value))

        print("  Params: ")
        for key, value in trial.params.items():
            print("    {}: {}".format(key, value))
            
        params = {'boosting_type': 'gbdt',
                  'objective': 'regression',
                  "metric": 'rmse'}
        for key, value in trial.params.items():
            params[key]=value
            
        dtrain = lgb.Dataset(train_x.iloc[trn_idx], label=train_y.iloc[trn_idx])
        dvalid = lgb.Dataset(train_x.iloc[val_idx], label=train_y.iloc[val_idx])
        model = lgb.train(params=params, train_set=dtrain,valid_sets=[dvalid],
                          verbose_eval=50,
                          early_stopping_rounds=20,
                          num_boost_round=5000)
        test_predict[:,i] = model.predict(test_x)
    predict = np.mean(test_predict,axis=1)

[I 2021-09-07 16:27:35,965] A new study created in memory with name: no-name-cc424a48-83c6-4329-92a3-261d08a5edb9
[I 2021-09-07 16:27:36,779] Trial 0 finished with value: 0.5178928385298298 and parameters: {'lambda_l1': 0.9464949700025425, 'lambda_l2': 1.4692321446797693e-05, 'num_leaves': 135, 'feature_fraction': 0.6448685329355106, 'bagging_fraction': 0.9048970068857253, 'bagging_freq': 7, 'min_child_samples': 30}. Best is trial 0 with value: 0.5178928385298298.
[I 2021-09-07 16:27:37,641] Trial 1 finished with value: 0.5336017055299863 and parameters: {'lambda_l1': 0.6354399847075458, 'lambda_l2': 4.87700419620481, 'num_leaves': 237, 'feature_fraction': 0.895991820221385, 'bagging_fraction': 0.6704364287317786, 'bagging_freq': 3, 'min_child_samples': 49}. Best is trial 0 with value: 0.5178928385298298.
[I 2021-09-07 16:27:38,288] Trial 2 finished with value: 0.5345721353318472 and parameters: {'lambda_l1': 9.52099217128906e-05, 'lambda_l2': 1.1454590646374039e-07, 'num_leaves': 170,

[I 2021-09-07 16:27:51,023] Trial 42 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:27:51,805] Trial 43 finished with value: 0.516065766031832 and parameters: {'lambda_l1': 0.00021869661941011055, 'lambda_l2': 1.0674672013946999e-08, 'num_leaves': 201, 'feature_fraction': 0.7039965594752932, 'bagging_fraction': 0.8165783106186105, 'bagging_freq': 1, 'min_child_samples': 10}. Best is trial 43 with value: 0.516065766031832.
[I 2021-09-07 16:27:51,940] Trial 44 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:27:52,044] Trial 45 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:27:52,218] Trial 46 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:27:53,067] Trial 47 finished with value: 0.5256815758791472 and parameters: {'lambda_l1': 6.162602167779085e-05, 'lambda_l2': 1.6462819728079273e-07, 'num_leaves': 201, 'feature_fraction': 0.7163097853297453, 'bagging_fraction': 0.9420618119436382, 'bagging_freq': 1, 'min_child_samples': 24}. Best is trial 

[I 2021-09-07 16:28:12,792] Trial 90 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:28:13,099] Trial 91 pruned. Trial was pruned at iteration 13.
[I 2021-09-07 16:28:13,456] Trial 92 pruned. Trial was pruned at iteration 14.
[I 2021-09-07 16:28:13,664] Trial 93 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:28:14,351] Trial 94 pruned. Trial was pruned at iteration 45.
[I 2021-09-07 16:28:14,508] Trial 95 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:28:14,828] Trial 96 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:28:14,962] Trial 97 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:28:16,197] Trial 98 finished with value: 0.5171555001746302 and parameters: {'lambda_l1': 1.0103137663726183e-08, 'lambda_l2': 1.7418953701287595e-06, 'num_leaves': 203, 'feature_fraction': 0.7265189263478641, 'bagging_fraction': 0.9317931154547426, 'bagging_freq': 1, 'min_child_samples': 10}. Best is trial 89 with value: 0.5102536883069437.
[I 2021

Number of finished trials: 100
Best trial:
  Value: 0.5102536883069437
  Params: 
    lambda_l1: 1.6446541932580473e-07
    lambda_l2: 1.0734412329614426e-07
    num_leaves: 193
    feature_fraction: 0.8123395009389368
    bagging_fraction: 0.9184649865458648
    bagging_freq: 1
    min_child_samples: 10
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000712 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1837
[LightGBM] [Info] Number of data points in the train set: 14860, number of used features: 8
[LightGBM] [Info] Start training from score 2.073247
Training until validation scores don't improve for 20 rounds
[50]	valid_0's rmse: 0.453164
[100]	valid_0's rmse: 0.442958
Early stopping, best iteration is:
[110]	valid_0's rmse: 0.442157


[I 2021-09-07 16:28:17,677] Trial 100 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:28:17,796] Trial 101 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:28:17,941] Trial 102 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:28:18,090] Trial 103 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:28:18,293] Trial 104 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:28:18,412] Trial 105 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:28:18,524] Trial 106 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:28:18,647] Trial 107 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:28:18,797] Trial 108 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:28:18,911] Trial 109 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:28:19,029] Trial 110 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:28:19,211] Trial 111 pruned. Trial was pruned at iteration 16.
[I 2021-09-07 16:28:19,595] Trial 112 pr

...

[I 2021-09-07 16:29:03,924] Trial 389 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:04,120] Trial 390 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:04,292] Trial 391 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:04,406] Trial 392 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:04,514] Trial 393 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:04,671] Trial 394 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:04,760] Trial 395 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:04,879] Trial 396 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:05,049] Trial 397 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:05,188] Trial 398 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:05,277] Trial 399 pruned. Trial was pruned at iteration 10.


Number of finished trials: 400
Best trial:
  Value: 0.5102536883069437
  Params: 
    lambda_l1: 1.6446541932580473e-07
    lambda_l2: 1.0734412329614426e-07
    num_leaves: 193
    feature_fraction: 0.8123395009389368
    bagging_fraction: 0.9184649865458648
    bagging_freq: 1
    min_child_samples: 10
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000424 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1838
[LightGBM] [Info] Number of data points in the train set: 14861, number of used features: 8
[LightGBM] [Info] Start training from score 2.063366
Training until validation scores don't improve for 20 rounds
[50]	valid_0's rmse: 0.458105
[100]	valid_0's rmse: 0.449598
[150]	valid_0's rmse: 0.449092
Early stopping, best iteration is:
[138]	valid_0's rmse: 0.448682


[I 2021-09-07 16:29:06,435] Trial 400 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:06,586] Trial 401 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:06,756] Trial 402 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:06,867] Trial 403 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:06,968] Trial 404 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:07,051] Trial 405 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:07,151] Trial 406 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:07,290] Trial 407 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:07,400] Trial 408 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:07,530] Trial 409 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:07,649] Trial 410 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:07,752] Trial 411 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:07,880] Trial 412 pr

[I 2021-09-07 16:29:19,892] Trial 489 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:20,026] Trial 490 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:20,152] Trial 491 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:20,291] Trial 492 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:20,385] Trial 493 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:20,508] Trial 494 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:20,644] Trial 495 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:20,766] Trial 496 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:20,912] Trial 497 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:21,093] Trial 498 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 16:29:21,228] Trial 499 pruned. Trial was pruned at iteration 10.


Number of finished trials: 500
Best trial:
  Value: 0.5102536883069437
  Params: 
    lambda_l1: 1.6446541932580473e-07
    lambda_l2: 1.0734412329614426e-07
    num_leaves: 193
    feature_fraction: 0.8123395009389368
    bagging_fraction: 0.9184649865458648
    bagging_freq: 1
    min_child_samples: 10
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001110 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1838
[LightGBM] [Info] Number of data points in the train set: 14861, number of used features: 8
[LightGBM] [Info] Start training from score 2.066924
Training until validation scores don't improve for 20 rounds
[50]	valid_0's rmse: 0.444941
[100]	valid_0's rmse: 0.437147
Early stopping, best iteration is:
[90]	valid_0's rmse: 0.43678
Wall time: 1min 46s


In [13]:
# 评估指标rmse，越小越好
np.sqrt(mean_squared_error(test_y,predict))

0.432341765333029

### 回归任务的结论
不使用optuna的RMSE分数是0.4346521330333544，使用的RMSE分数是0.432341765333029，提升了0.0023103677003254。

作者测了很多次，基本在0.003-0.002之间，感兴趣的可以多跑几次。

## 森林植被类型（多分类）

In [25]:
import numpy as np
import pandas as pd
import time
import gc

from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.preprocessing import OrdinalEncoder
import lightgbm as lgb  # 使用lgb模型

In [26]:
from sklearn.datasets import fetch_covtype
data = fetch_covtype()
X, y = data['data'], data['target']
X = pd.DataFrame(X,columns=data.feature_names)
print('七分类任务，处理前：',np.unique(y))
print(y)
ord = OrdinalEncoder()
y = ord.fit_transform(y.reshape(-1, 1))
y = y.reshape(-1, )
print('七分类任务，处理后：',np.unique(y))
print(y)
X.head(2)

七分类任务，处理前： [1 2 3 4 5 6 7]
[5 5 2 ... 3 3 3]
七分类任务，处理后： [0. 1. 2. 3. 4. 5. 6.]
[4. 4. 1. ... 2. 2. 2.]


Elevation  Aspect  Slope  Horizontal_Distance_To_Hydrology  \
0     2596.0    51.0    3.0                             258.0   
1     2590.0    56.0    2.0                             212.0   

   Vertical_Distance_To_Hydrology  Horizontal_Distance_To_Roadways  \
0                             0.0                            510.0   
1                            -6.0                            390.0   

   Hillshade_9am  Hillshade_Noon  Hillshade_3pm  \
0          221.0           232.0          148.0   
1          220.0           235.0          151.0   

   Horizontal_Distance_To_Fire_Points  ...  Soil_Type_30  Soil_Type_31  \
0                              6279.0  ...           0.0           0.0   
1                              6225.0  ...           0.0           0.0   

   Soil_Type_32  Soil_Type_33  Soil_Type_34  Soil_Type_35  Soil_Type_36  \
0           0.0           0.0           0.0           0.0           0.0   
1           0.0           0.0           0.0           0.0           0.0   

   Soil_Type_37  Soil_Type_38  Soil_Type_39  
0           0.0           0.0           0.0  
1           0.0           0.0           0.0  

[2 rows x 54 columns]

In [15]:
X.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 581012 entries, 0 to 581011
Data columns (total 54 columns):
 #   Column                              Non-Null Count   Dtype  
---  ------                              --------------   -----  
 0   Elevation                           581012 non-null  float64
 1   Aspect                              581012 non-null  float64
 2   Slope                               581012 non-null  float64
 3   Horizontal_Distance_To_Hydrology    581012 non-null  float64
 4   Vertical_Distance_To_Hydrology      581012 non-null  float64
 5   Horizontal_Distance_To_Roadways     581012 non-null  float64
 6   Hillshade_9am                       581012 non-null  float64
 7   Hillshade_Noon                      581012 non-null  float64
 8   Hillshade_3pm                       581012 non-null  float64
 9   Horizontal_Distance_To_Fire_Points  581012 non-null  float64
 10  Wilderness_Area_0                   581012 non-null  float64
 11  Wilderness_Area_1         

In [27]:
# 切分训练和测试集
train_x, test_x, train_y, test_y = train_test_split(X, y,random_state=42,test_size=0.1)
train_y = pd.DataFrame(train_y,columns=['result'])
test_y = pd.DataFrame(test_y,columns=['result'])

print('训练集：',train_x.shape)
print('测试集：', test_x.shape)

训练集： (522910, 54)
测试集： (58102, 54)


In [28]:
from sklearn.model_selection import StratifiedKFold
skf = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)

In [58]:
%%time
test_predict = 0
params = {"boosting_type": "gbdt",
          "objective": "multiclass",
          "num_class': 7,
          "metric": "multi_logloss"}
for i, (trn_idx, val_idx) in enumerate(skf.split(train_x, train_y)):
    dtrain = lgb.Dataset(train_x.iloc[trn_idx], label=train_y.iloc[trn_idx])
    dvalid = lgb.Dataset(train_x.iloc[val_idx], label=train_y.iloc[val_idx])
    model = lgb.train(params=params, train_set=dtrain,valid_sets=[dvalid],
                      verbose_eval=50,
                      early_stopping_rounds=20,
                      num_boost_round=5000)
    test_predict += model.predict(test_x)
predict = test_predict/5

[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.030610 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2264
[LightGBM] [Info] Number of data points in the train set: 418328, number of used features: 53
[LightGBM] [Info] Start training from score -1.009534
[LightGBM] [Info] Start training from score -0.717940
[LightGBM] [Info] Start training from score -2.789075
[LightGBM] [Info] Start training from score -5.347629
[LightGBM] [Info] Start training from score -4.112163
[LightGBM] [Info] Start training from score -3.508300
[LightGBM] [Info] Start training from score -3.343939
Training until validation scores don't improve for 20 rounds
[50]	valid_0's multi_logloss: 0.424906
[100]	valid_0's multi_logloss: 0.413801
Early stopping, best iteration is:
[90]	valid_0's multi_logloss: 0.37472
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.031196 seconds.
You can s

In [62]:
# 评估指标acc，越大越好
print('不使用optuna的多分类分数：', accuracy_score(np.argmax(predict, axis=1), test_y))

不使用optuna的多分类分数： 0.8631716636260369


In [70]:
import optuna
def objective(trial,train_x, train_y, valid_x, valid_y):
    dtrain = lgb.Dataset(train_x, label=train_y)
    dvalid = lgb.Dataset(valid_x, label=valid_y)

    param = {
        "objective": "multiclass",
        "metric": "multi_logloss",
        "verbosity": -1,
        "num_class": 7,
        "boosting_type": "gbdt",
        'random_state':42,
        "lambda_l1": trial.suggest_float("lambda_l1", 1e-8, 10.0, log=True),
        "lambda_l2": trial.suggest_float("lambda_l2", 1e-8, 10.0, log=True),
        "num_leaves": trial.suggest_int("num_leaves", 2, 256),
        "feature_fraction": trial.suggest_float("feature_fraction", 0.4, 1.0),
        "bagging_fraction": trial.suggest_float("bagging_fraction", 0.4, 1.0),
        "bagging_freq": trial.suggest_int("bagging_freq", 1, 7),
        "min_child_samples": trial.suggest_int("min_child_samples", 5, 100),
    }

    # Add a callback for pruning.
    pruning_callback = optuna.integration.LightGBMPruningCallback(trial, "multi_logloss")
    gbm = lgb.train(
        param, dtrain, valid_sets=[dvalid], verbose_eval=False, callbacks=[pruning_callback]
    )

    preds = gbm.predict(valid_x)
    pred_labels = np.rint(preds)
    acc = accuracy_score(np.argmax(pred_labels, axis=1), valid_y)
    return acc

In [72]:
%%time
if __name__ == "__main__":
    test_predict = 0
    study = optuna.create_study(
        pruner=optuna.pruners.MedianPruner(n_warmup_steps=10), direction="minimize"  # 指定是越小越好
    )
    for i, (trn_idx, val_idx) in enumerate(skf.split(train_x, train_y)):
        study.optimize(lambda trial: objective(trial, train_x.iloc[trn_idx], train_y.iloc[trn_idx], 
                                               train_x.iloc[val_idx], train_y.iloc[val_idx]), n_trials=100)

        print("Number of finished trials: {}".format(len(study.trials)))

        print("Best trial:")
        trial = study.best_trial

        print("  Value: {}".format(trial.value))

        print("  Params: ")
        for key, value in trial.params.items():
            print("    {}: {}".format(key, value))
            
        params = {"boosting_type": "gbdt",
                  "objective": "multiclass",
                  "num_class": 7,
                  "metric": "multi_logloss"}
        for key, value in trial.params.items():
            params[key]=value
            
        dtrain = lgb.Dataset(train_x.iloc[trn_idx], label=train_y.iloc[trn_idx])
        dvalid = lgb.Dataset(train_x.iloc[val_idx], label=train_y.iloc[val_idx])
        model = lgb.train(params=params, train_set=dtrain,valid_sets=[dvalid],
                          verbose_eval=50,
                          early_stopping_rounds=20,
                          num_boost_round=5000)
        test_predict += model.predict(test_x)
    predict = test_predict/5

[I 2021-09-07 18:21:48,373] A new study created in memory with name: no-name-7584aee7-d7a5-42ce-8426-7d4c7e034372
[I 2021-09-07 18:22:17,890] Trial 0 finished with value: 0.8652253733912145 and parameters: {'lambda_l1': 0.00029350441808598135, 'lambda_l2': 0.0050140304157587625, 'num_leaves': 41, 'feature_fraction': 0.7195254545980898, 'bagging_fraction': 0.6783357374559799, 'bagging_freq': 6, 'min_child_samples': 32}. Best is trial 0 with value: 0.8652253733912145.
[I 2021-09-07 18:22:40,277] Trial 1 finished with value: 0.865770400260083 and parameters: {'lambda_l1': 8.073501039689362e-07, 'lambda_l2': 2.7820830665481296e-05, 'num_leaves': 41, 'feature_fraction': 0.8160512302334224, 'bagging_fraction': 0.6156688842906214, 'bagging_freq': 7, 'min_child_samples': 35}. Best is trial 0 with value: 0.8652253733912145.
[I 2021-09-07 18:23:14,303] Trial 2 finished with value: 0.9372358532060967 and parameters: {'lambda_l1': 1.1987047256838896e-07, 'lambda_l2': 0.0008429364945676234, 'num_le

[I 2021-09-07 18:33:02,134] Trial 52 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 18:33:25,476] Trial 53 pruned. Trial was pruned at iteration 75.
[I 2021-09-07 18:33:30,367] Trial 54 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 18:33:34,302] Trial 55 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 18:33:40,033] Trial 56 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 18:33:43,381] Trial 57 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 18:33:47,728] Trial 58 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 18:33:52,240] Trial 59 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 18:33:56,752] Trial 60 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 18:34:02,449] Trial 61 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 18:34:07,140] Trial 62 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 18:34:13,623] Trial 63 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 18:34:19,092] Trial 64 pruned. Trial w

Number of finished trials: 100
Best trial:
  Value: 0.8423533686485246
  Params: 
    lambda_l1: 6.031700696477528e-05
    lambda_l2: 0.24394450720600092
    num_leaves: 33
    feature_fraction: 0.48861458318031864
    bagging_fraction: 0.9555014696451426
    bagging_freq: 1
    min_child_samples: 79
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.023061 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2262
[LightGBM] [Info] Number of data points in the train set: 418328, number of used features: 52
[LightGBM] [Info] Start training from score -1.009534
[LightGBM] [Info] Start training from score -0.717940
[LightGBM] [Info] Start training from score -2.789075
[LightGBM] [Info] Start training from score -5.347629
[LightGBM] [Info] Start training from score -4.112163
[LightGBM] [Info] Start training from score -3.508300
[LightGBM] [Info] Start training from score -3.343939
Training until validation s

[3350]	valid_0's multi_logloss: 0.107463
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[3400]	valid_0's multi_logloss: 0.107071
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[3450]	valid_0's multi_logloss: 0.106658
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[3500]	valid_0's multi_logloss: 0.106334
[LightGBM] 

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[4450]	valid_0's multi_logloss: 0.100337
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[4500]	valid_0's multi_logloss: 0.100081
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warnin

...

[I 2021-09-07 20:39:58,219] Trial 483 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 20:40:02,806] Trial 484 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 20:40:09,290] Trial 485 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 20:40:49,570] Trial 486 finished with value: 0.9436040618844543 and parameters: {'lambda_l1': 0.00020397245265135663, 'lambda_l2': 9.093796518313558e-06, 'num_leaves': 214, 'feature_fraction': 0.8663304164529336, 'bagging_fraction': 0.6476610679220174, 'bagging_freq': 4, 'min_child_samples': 87}. Best is trial 3 with value: 0.8423533686485246.
[I 2021-09-07 20:40:54,931] Trial 487 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 20:41:00,439] Trial 488 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 20:41:05,860] Trial 489 pruned. Trial was pruned at iteration 13.
[I 2021-09-07 20:41:10,637] Trial 490 pruned. Trial was pruned at iteration 10.
[I 2021-09-07 20:41:15,141] Trial 491 pruned. Trial was pruned at iteration 10.


Number of finished trials: 500
Best trial:
  Value: 0.8423533686485246
  Params: 
    lambda_l1: 6.031700696477528e-05
    lambda_l2: 0.24394450720600092
    num_leaves: 33
    feature_fraction: 0.48861458318031864
    bagging_fraction: 0.9555014696451426
    bagging_freq: 1
    min_child_samples: 79
[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.025451 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2268
[LightGBM] [Info] Number of data points in the train set: 418328, number of used features: 53
[LightGBM] [Info] Start training from score -1.009528
[LightGBM] [Info] Start training from score -0.717945
[LightGBM] [Info] Start training from score -2.789114
[LightGBM] [Info] Start training from score -5.348131
[LightGBM] [Info] Start training from score -4.112163
[LightGBM] [Info] Start training from score -3.508220
[LightGBM] [Info] Start training from score -3.343871
Training until validation s

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[3450]	valid_0's multi_logloss: 0.107511
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[3500]	valid_0's multi_logloss: 0.107145
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warnin

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[4300]	valid_0's multi_logloss: 0.102136
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[4350]	valid_0's multi_logloss: 0.101919
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warnin

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[4950]	valid_0's multi_logloss: 0.0993946
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain,

In [73]:
# 评估指标acc，越大越好
print('使用optuna的多分类分数：', accuracy_score(np.argmax(predict, axis=1), test_y))

使用optuna的多分类分数： 0.968056177067915


### 分类任务的结论
不使用optuna的ACC分数是0.8631716636260369，使用的ACC分数是0.968056177067915，提升了0.1048845134418781。

结合Stacking.ipynb里的单模随机森林最好分数0.9535087055000585甚至Stacking后的融合分数0.9589887988544127进行对比，也都是上涨的。